<a href="https://colab.research.google.com/github/MiguelAndresPena/Senales_y_Sistemas/blob/main/Libro_5_Clases.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Filtro Pasabanda para Audio Usando Filtros IIR

Este notebook implementa un filtro pasabanda para una canción descargada desde YouTube. Se utilizan los siguientes filtros IIR:
- Butterworth
- Chebyshev Tipo I
- Chebyshev Tipo II
- Bessel
- Elíptico



In [ ]:
# Paso 0: Instalación (solo es necesario ejecutar una vez)
!python3 -m pip install --force-reinstall https://github.com/yt-dlp/yt-dlp/archive/master.tar.gz
!apt install ffmpeg  # En caso de error con ffmpeg
!pip install soundfile scipy matplotlib numpy

# Paso 1: Descargar canción desde YouTube
link = "https://www.youtube.com/watch?v=_ghCnV_z7Vc"
!yt-dlp --extract-audio -o "audio" --audio-format mp3 {link}
!ffmpeg -i audio.mp3 output.wav

# Paso 2: Leer el archivo de audio
import soundfile as sf
import numpy as np
from IPython.display import Audio
import scipy.signal as signal
import matplotlib.pyplot as plt

# Leer el archivo WAV
x, fs = sf.read("output.wav")
print(f"Frecuencia de muestreo: {fs} Hz")
print(f"Duración total: {x.shape[0]/fs:.2f} segundos")

# Paso 3: Extraer 10 segundos de la canción
ti = 30  # segundo de inicio
tf = ti + 10
x_segmento = x[int(ti*fs):int(tf*fs), :]
x_mono = np.mean(x_segmento, axis=1)  # Convertir a mono

# Para escuchar el segmento original
Audio(x_mono, rate=fs)

  Using cached https://github.com/yt-dlp/yt-dlp/archive/master.tar.gz (2.8 MB)
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for yt-dlp: filename=yt_dlp-2025.6.30-py3-none-any.whl size=3017662 sha256=111fbd155e3fea8f05c9d8ebf7d70210c4060058f9fef16e28280480145b802a
  Stored in directory: /tmp/pip-ephem-wheel-cache-izzxwvwe/wheels/2d/79/97/7209650ef73114e0fe0603480da012ad3afacb9cae6b8acd9a
Successfully built yt-dlp
  Attempting uninstall: yt-dlp
    Found existing installation: yt-dlp 2025.6.30
    Uninstalling yt-dlp-2025.6.30:
      Successfully uninstalled yt-dlp-2025.6.30
Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
ffmpeg is already the newest version (7:4.4.2-0ubuntu0.22.04.1).
0 upgraded, 0 newly installed, 0 to remove and 35 not upgraded.
[youtube] Extracting URL: https://www.youtube.com/watch?v=C2q7lB0NRBk
[youtube] C2q7lB0N

In [ ]:
# Función para diseñar filtros IIR
def diseño_filtro_iir(tipo, fs, lowcut, highcut, orden=5):
    nyq = 0.5 * fs
    low = lowcut / nyq
    high = highcut / nyq

    if tipo == 'butter':
        b, a = signal.iirfilter(orden, [low, high], btype='band', ftype='butter')
    elif tipo == 'cheby1':
        b, a = signal.iirfilter(orden, [low, high], btype='band', ftype='cheby1', rp=1)
    elif tipo == 'cheby2':
        b, a = signal.iirfilter(orden, [low, high], btype='band', ftype='cheby2', rs=40)
    elif tipo == 'ellip':
        b, a = signal.iirfilter(orden, [low, high], btype='band', ftype='ellip', rp=1, rs=40)
    elif tipo == 'bessel':
        b, a = signal.iirfilter(orden, [low, high], btype='band', ftype='bessel', output='ba')
    else:
        raise ValueError("Tipo de filtro no válido")

    return b, a

# Parámetros del filtro
lowcut = 500  # Hz
highcut = 3000  # Hz

# Aplicar filtros y guardar audios
tipos = ['butter', 'cheby1', 'cheby2', 'ellip', 'bessel']
audios_filtrados = {}

for tipo in tipos:
    b, a = diseño_filtro_iir(tipo, fs, lowcut, highcut)
    y = signal.filtfilt(b, a, x_mono)
    audios_filtrados[tipo] = y


In [ ]:
# FIR con firwin
def filtro_firwin(fs, lowcut, highcut, numtaps=101):
    nyq = 0.5 * fs
    taps = signal.firwin(numtaps, [lowcut / nyq, highcut / nyq], pass_zero=False)
    return taps

taps = filtro_firwin(fs, lowcut, highcut)
y_fir = signal.filtfilt(taps, [1.0], x_mono)
audios_filtrados['firwin'] = y_fir


In [ ]:
# Butterworth
print("🔊 Audio filtrado con Butterworth:")
Audio(audios_filtrados['butter'], rate=fs)

🔊 Audio filtrado con Butterworth:


In [ ]:
# Chebyshev tipo 1
print("🔊 Audio filtrado con Chebyshev Tipo I:")
Audio(audios_filtrados['cheby1'], rate=fs)

🔊 Audio filtrado con Chebyshev Tipo I:


In [ ]:
# Chebyshev tipo 2
print("🔊 Audio filtrado con Chebyshev Tipo II:")
Audio(audios_filtrados['cheby2'], rate=fs)

🔊 Audio filtrado con Chebyshev Tipo II:


In [ ]:
# Bessel
print("🔊 Audio filtrado con Bessel:")
Audio(audios_filtrados['bessel'], rate=fs)

🔊 Audio filtrado con Bessel:


In [ ]:
# Elíptico
print("🔊 Audio filtrado con Elíptico:")
Audio(audios_filtrados['ellip'], rate=fs)

🔊 Audio filtrado con Elíptico:


In [ ]:
# FIR con firwin
print("🔊 Audio filtrado con FIR (firwin):")
Audio(audios_filtrados['firwin'], rate=fs)

🔊 Audio filtrado con FIR (firwin):


In [ ]:
# Comparar espectros de los filtros
plt.figure(figsize=(10,6))
for nombre, señal in audios_filtrados.items():
    f, Pxx = signal.welch(señal, fs, nperseg=1024)
    plt.semilogy(f, Pxx, label=nombre)

plt.title("Espectros de potencia de señales filtradas")
plt.xlabel("Frecuencia (Hz)")
plt.ylabel("Densidad espectral")
plt.legend()
plt.grid()
plt.tight_layout()
plt.show()


#📘 Punto 2: Diseño de Filtros FIR por Ventaneo y Comparación FIR vs IIR

### ¿En qué consiste el diseño de filtros FIR por ventaneo?

El diseño de filtros FIR por ventana consiste en aproximar una respuesta ideal en frecuencia (como un filtro pasa bajas ideal) mediante una respuesta finita en el tiempo. Para ello se usa una función ventana que **suaviza** el truncamiento de la respuesta ideal.

Esto se puede implementar fácilmente en Python usando la función `firwin` de `scipy.signal`.





# ✳️ Propiedades de los Filtros FIR

- La función de transferencia de un filtro FIR es:

$$
H(z) = b_0 + b_1 z^{-1} + b_2 z^{-2} + \cdots + b_N z^{-N}
$$

- Esto significa que:

  - ✅ **Tiene _solo ceros_** (no tiene polos, salvo en el origen).
  - ✅ **Es _siempre estable_**.
  - ✅ Puede tener **_fase lineal exacta_** si sus coeficientes son simétricos.
  - ✅ Su diseño es **_simple y directo_** mediante métodos como `firwin`, `remez`, etc.


| **Criterio**                  | **Filtros FIR**                                         | **Filtros IIR**                                      |
| ----------------------------- | ------------------------------------------------------- | ---------------------------------------------------- |
| **Estabilidad**               | Siempre estables (solo ceros)                           | Pueden ser inestables (tienen polos)                 |
| **Fase lineal**               | Posible con diseño simétrico                            | Generalmente no tienen fase lineal                   |
| **Complejidad computacional** | Mayor (requieren más coeficientes para misma respuesta) | Menor (logran buena respuesta con menos orden)       |
| **Diseño**                    | Sencillo (firwin, remez, etc.)                          | Requiere cuidado con la ubicación de polos y ceros   |
| **Respuesta en frecuencia**   | Transición más suave (menos selectividad por orden)     | Transiciones más abruptas y precisas con menor orden |
| **Precisión en el diseño**    | Menor precisión frecuencial por orden                   | Alta precisión gracias a los polos                   |
| **Aplicaciones comunes**      | Audio, señales biológicas, comunicaciones               | Control automático, procesamiento en tiempo real     |
